# VCT regression model with modular model

In [ ]:
import warnings
warnings.filterwarnings('ignore')
%matplotlib inline
%load_ext autoreload
%autoreload 2
#%config Completer.use_jedi = False

In [3]:
import pandas as pd
pd.set_option('display.max_rows', 5000)
pd.set_option('display.max_columns', 5000)
pd.set_option('display.width', 10000)
import numpy as np
import yaml

from vessel_manoeuvring_models.visualization.plot import track_plot, plot
from phd.visualization.plot_ship import track_plots
from vessel_manoeuvring_models.extended_kalman_vmm import ExtendedKalman, SystemMatrixes
from vmm_abkowitz_diminished import vmm as vmm
from wPCC_pipeline.pipelines.brix.nodes import initial_parameters, extract_added_masses
from wPCC_pipeline.pipelines.preprocess.nodes import load, add_thrust
from wPCC_pipeline.pipelines.filter_data_extended_kalman.nodes import guess_covariance_matrixes, initial_state, extended_kalman_filter, extended_kalman_smoother
from wPCC_pipeline.pipelines.motion_regression.nodes import predict_force, fit_motions, create_model_from_motion_regression
from wPCC_pipeline.pipelines.prediction.nodes import simulate_euler
from phd.pipelines.load_7m.nodes import fix_interpolated_angle
from sklearn.metrics import mean_squared_error
from vessel_manoeuvring_models.models.vmm import VMM, Simulator, ModelSimulator, get_coefficients
import sympy as sp
from functools import reduce
from operator import add
from vessel_manoeuvring_models.symbols import *
import vessel_manoeuvring_models.symbols as symbols
from vessel_manoeuvring_models.models.propeller import *
from vessel_manoeuvring_models.models.semiempirical_rudder import SemiempiricalRudderSystem
from IPython.display import display
from vessel_manoeuvring_models.prime_system import df_prime
from vessel_manoeuvring_models.substitute_dynamic_symbols import run, lambdify
from vessel_manoeuvring_models.models.modular_simulator import ModularVesselSimulator
from vessel_manoeuvring_models.models.subsystem import PrimeEquationSubSystem, EquationSubSystem
from vessel_manoeuvring_models.parameters import df_parameters
from phd.helpers import mean
from vessel_manoeuvring_models.angles import mean_angle
from vessel_manoeuvring_models.angles import smallest_signed_angle
from vessel_manoeuvring_models.models.diff_eq_to_matrix import DiffEqToMatrix
from vessel_manoeuvring_models import prime_system
from vessel_manoeuvring_models.models.modular_simulator import subs_simpler
import statsmodels.api as sm
from wPCC_pipeline.pipelines.vct_data.nodes import vct_scaling
from vct.bokeh_plotting import create_tab
from wPCC_pipeline.pipelines.vct_data.nodes import vct_scaling
import inspect
from sympy.printing import pretty
p = df_parameters["symbol"]

import logging
log = logging.getLogger(__name__)

import matplotlib.pyplot as plt
plt.style.use('bmh')

[07/06/23 13:52:31] WARNING  /home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/bokeh/core/p ]8;id=726443;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=371680;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py#109\109]8;;\
                             roperty/primitive.py:37: DeprecationWarning: `np.bool8` is a                          
                             deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)                             
                               bokeh_bool_types += (np.bool8,)                                                     
                                                                                                                   

[07/06/23 13:52:32] WARNING  /home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/bokeh/io/not ]8;id=969596;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=311210;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py#109\109]8;;\
                             ebook.py:487: DeprecationWarning: The `source` parameter emit a                       
                             deprecation warning since IPython 8.0, it had no effects for a long                   
                             time and will  be removed in future versions.                                         
                               publish_display_data(data, metadata, source, transient=transient,                   
                             **kwargs)                                                                             
                                                                                                                   

Loading BokehJS ...

In [4]:
%reload_kedro
ship='wPCC'
df_VCT = catalog.load(f"{ship}.df_VCT")
ship_data = catalog.load(f"{ship}.ship_data")
df_VCT = vct_scaling(data=df_VCT, ship_data=ship_data)
df_VCT['U'] = df_VCT['V']

thrust_keys = catalog.load(f"params:wPCC.thrust_keys")
exclude_parameters = catalog.load(f"params:{ship}.exclude_parameters")
model_loaders = catalog.load(f"{ship}.models")

df_VCT.sort_values(by=['test type','V','delta','v'], inplace=True)

                    INFO     Resolved project path as: /home/maa/dev/PHD.                           ]8;id=885689;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=931692;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py#134\134]8;;\
                             To set a different path, run '%reload_kedro <project_root>'                           

                    WARNING  /home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/framew ]8;id=386572;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=678754;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py#109\109]8;;\
                             ork/startup.py:98: DeprecationWarning: project_version in                             
                             pyproject.toml is deprecated, use kedro_init_version instead                          
                               warnings.warn(                                                                      
                                                                                                                   

[07/06/23 13:52:38] INFO     Kedro project phd                                                      ]8;id=938589;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=932675;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py#103\103]8;;\

                    INFO     Defined global variable 'context', 'session', 'catalog' and            ]8;id=526888;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=103477;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py#104\104]8;;\
                             'pipelines'                                                                           

                    INFO     Registered line magic 'run_viz'                                        ]8;id=914556;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=686823;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/ipython/__init__.py#110\110]8;;\

                    INFO     Loading data from 'wPCC.df_VCT' (CSVDataSet)...                    ]8;id=431991;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=349181;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\

                    INFO     Loading data from 'wPCC.ship_data' (YAMLDataSet)...                ]8;id=57458;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=873524;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\

                    INFO     Loading data from 'params:wPCC.thrust_keys' (MemoryDataSet)...     ]8;id=661736;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=205240;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\

                    INFO     Loading data from 'params:wPCC.exclude_parameters'                 ]8;id=492096;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=453415;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\
                             (MemoryDataSet)...                                                                    

                    INFO     Loading data from 'wPCC.models' (PartitionedDataSet)...            ]8;id=710866;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=826691;file:///home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\

## Compare with MDL model

In [8]:
model_MDL = model_loaders["MDL_modular_propeller_rudder_wind"]()
model_MDL.ship_parameters['A_XV'] = 0
model_MDL.ship_parameters['A_YV'] = 0
model_MDL.subsystems['hull'].V0=0


In [11]:
states=df_VCT[['u','v','r']].copy()
states['x0'] = 0
states['y0'] = 0
states['psi'] = 0

control=df_VCT[['delta','rev']].copy()
control['twa'] = 0
control['tws'] = 0
control['rev'] = 7


df_prediction = pd.DataFrame(model_MDL.calculate_forces(states_dict=states, control=control))
df_prediction = pd.merge(left=df_prediction, right=df_VCT, how='left', left_index=True, right_index=True, suffixes=('','_vct'))
df_prediction['fx_hull'] = df_prediction['X_H']
df_prediction['fy_hull'] = df_prediction['Y_H']
df_prediction['mz_hull'] = df_prediction['N_H']


In [12]:
df_prediction['fx'] = run(model_MDL.lambda_X_D, inputs=df_prediction)
df_prediction['fy'] = run(model_MDL.lambda_Y_D, inputs=df_prediction)
df_prediction['mz'] = run(model_MDL.lambda_N_D, inputs=df_prediction)
df_prediction['model_name'] = 'MDL model'


In [14]:
results = pd.concat((df_VCT, df_prediction), axis=0)

In [15]:
create_tab(df_VCT=results, ys=['fx_hull', 'fy_hull', 'mz_hull'])

[07/06/23 14:07:55] WARNING  /home/maa/anaconda3/envs/phd/lib/python3.10/site-packages/bokeh/io/not ]8;id=910007;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=856847;file:///home/maa/anaconda3/envs/phd/lib/python3.10/warnings.py#109\109]8;;\
                             ebook.py:487: DeprecationWarning: The `source` parameter emit a                       
                             deprecation warning since IPython 8.0, it had no effects for a long                   
                             time and will  be removed in future versions.                                         
                               publish_display_data(data, metadata, source, transient=transient,                   
                             **kwargs)                                                                             
                                                                                                                   

Tabs(id='6320', ...)